# A. EDINET APIを用いてXBRLデータを取得する
'Dropbox\TSR_RA_Ochiai\Note\EDINET\EDINET_API仕様書.pdf'を参照

## 1. 書類一覧APIから検索する書類を抽出する
エンドポイント：'https://disclosure.edinet-fsa.go.jp/api/v1/documents.json'<br>
HTTPメソッド：GETメソッド<br>
バージョン：'v1'を使用<br>
リクエストパラメータ：
- date：YYYY-MM-DDで日付を指定
- type：1→メタデータのみ、2→提出書類一覧及びメタデータを取得

In [28]:
import pandas as pd
import requests
import datetime
import zipfile
import glob
import os
import pickle
from arelle import ModelManager
from arelle import Cntlr

### 期間を指定する関数

In [2]:
def make_day_list(start_date, end_date):
    """開始日時と終了日時を設定すると、期間内の日付がすべて入ったリストが返される

    Args:
        start_date (datetime.date): 開始日時
        end_date (datetime.date): 終了日時

    Returns:
        list: 開始日時から終了日時までのすべての日付が格納されたリスト
    """
    period = int((end_date - start_date).days)
    day_list = []
    for d in range(period):
        day = start_date + datetime.timedelta(days=d)
        day_list.append(day)
    
    day_list.append(end_date)
    print(f'start_date is {day_list[0]}')
    print(f'end_date is {day_list[-1]}')
    print(f'period is {period} days')

    return day_list

### データを取得する期間を設定し、該当期間に提出された書類一覧(ID)を取得する

In [66]:
def save_doc_id(start_date, end_date, fc, oc, path):
    """書類情報を取得する

    Args:
        start_date (datetime.date): start date
        end_date (datetime.date): end date
        fc (str): formCode (様式コード)
        oc (str): ordinanceCode (府令コード)
        path (str): pickleオブジェクト保存先のパス
    """
    # データを取得する期間の設定
    day_list = make_day_list(start_date, end_date)

    # メタデータと提出書類一覧をJSON形式で取得
    id_list = []
    for day in day_list:
        print(day)
        params = {'type': 2, 'date': day}
        url = 'https://disclosure.edinet-fsa.go.jp/api/v1/documents.json'
        meta_data = requests.get(url=url, params=params)
        if meta_data.status_code == 200:
            meta_data_json = meta_data.json()
            meta_data_df = pd.json_normalize(meta_data_json)
            c = meta_data_df['metadata.resultset.count']
            if not int(c) == 0:
                results = pd.DataFrame(meta_data_json['results'])
                results = results[(results['ordinanceCode'] == oc) & (results['formCode'] == fc)]
                id = list(results['docID'])
                id_list.append(id)

    with open(path, mode='wb') as file:
        pickle.dump(id_list, file)

In [ ]:
start_date = datetime.date(2017, 1, 1)
end_date = datetime.date(2021, 9, 15)
path = 'C:/Users/koeci/Google ドライブ/MBA/ワークショップ/data/EDINET/download_list/download_list_new_release.pickle'
save_doc_id(start_date, end_date, fc='024000', oc='010', path=path)

## 2. 書類取得APIからXBRLデータを取得する
エンドポイント：'https://disclosure.edinet-fsa.go.jp/api/v1/documents/書類管理番号'  
HTTPSメソッド：GETメソッド  
バージョン：'v1'を使用  
リクエストパラメータ：
- type：1→提出本文書及び監査報告書(XBRLファイルを含む)、2→PDFを取得、3→代替書面・添付文書を取得、4→英文ファイルを取得

### 試しに、１社のみでzipファイルをダウンロードしてみる

In [63]:
# 1社で試しにダウンロードしてみる→zipファイルがダウンロードされる
id = docID_list[0]
params = {'type': 1}
url = 'https://disclosure.edinet-fsa.go.jp/api/v1/documents/' + id
doc = requests.get(url=url, params=params, stream=True)

filename = '../../Data/EDINET/API_data/' + id + '.zip'
if doc.status_code == 200:
    with open(file=filename, mode='wb') as file:
        file.write(doc.content)

### １で取得したIDのリストを元に、すべての企業・すべての期間のzipファイルをダウンロードする

In [68]:
def download_zip(pickle_path, save_path, start=0):
    import time

    # 書類管理番号を取得する
    with open(pickle_path, mode='rb') as file:
        id_list = pickle.load(file)
    docID_list = [k for i in id_list for k in i]
    docID_list = docID_list[start:]

    # 書類管理番号ごとに書類を取得する
    params = {'type': 1}
    sum_all = len(docID_list)

    for i, id in enumerate(docID_list):
        print(f'{i + 1} / {sum_all} was saved.')
        url = 'https://disclosure.edinet-fsa.go.jp/api/v1/documents/' + id
        doc = requests.get(url=url, params=params)
        filename = save_path + id + '.zip'
        # HTTPリクエストが正しく処理された場合にファイルの作成を実行
        if doc.status_code == 200:
            with open(filename, mode='wb') as file:
                content = doc.content
                file.write(content)
        time.sleep(0.6)

In [ ]:
pickle_path = 'C:/Users/koeci/Google ドライブ/MBA/ワークショップ/data/EDINET/download_list/download_list_new_release.pickle'
save_path = 'D:/Workshop_Data/new_release/'
download_zip(pickle_path=pickle_path, save_path=save_path, start=0)

### 途中で処理落ちした時は、以下のセルで"start"にエラーしたファイル番号を入力して実行する
ファイル番号は上のセルで順次出力されるため、最後の番号を入力すればよい

# B. 取得したXBRLデータから財務情報を抽出する

参考：https://qiita.com/XBRLJapan/items/b1e66f79d597df7b6037

## 1. zipファイルの解凍

In [18]:
def unzip(zip_path):
    for i, f in enumerate(zip_files):
        len_zip_files = len(zip_files)
        try:
            with zipfile.ZipFile(f) as zip_f:
                zip_f.extractall(zip_path)
            print(f'file:{f}, successfully loaded {i + 1} / {len_zip_files}')
        except zipfile.BadZipFile:
            print(f'file:{f}, could not load {i + 1} / {len_zip_files} ')            

In [34]:
# 以下のコマンドでzipファイルがすべて展開されるので実行には注意
for year in ['2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017_2021']:
    zip_path = 'D:/Workshop_Data/securities/' + str(year) + '/'
    zip_files = glob.glob(os.path.join(zip_path, '*.zip'))
    unzip(zip_path)

file:D:/Workshop_Data/securities/2008\1301_20080626_有価証券報告書‐第85期（平成19年4月1日‐平成20年3月31日）.zip, could not load 1 / 2846 
file:D:/Workshop_Data/securities/2008\1332_20080626_有価証券報告書‐第93期（平成19年4月1日‐平成20年3月31日）.zip, could not load 2 / 2846 
file:D:/Workshop_Data/securities/2008\1334_20080625_有価証券報告書‐第4期（平成19年4月1日‐平成20年3月31日）.zip, could not load 3 / 2846 
file:D:/Workshop_Data/securities/2008\1352_20080625_有価証券報告書‐第73期（平成19年4月1日‐平成20年3月31日）.zip, could not load 4 / 2846 
file:D:/Workshop_Data/securities/2008\1376_20080829_有価証券報告書‐第61期（平成19年6月1日‐平成20年5月31日）.zip, could not load 5 / 2846 
file:D:/Workshop_Data/securities/2008\1377_20080828_有価証券報告書‐第67期（平成19年6月1日‐平成20年5月31日）.zip, could not load 6 / 2846 
file:D:/Workshop_Data/securities/2008\1380_20080626_有価証券報告書‐第29期（平成19年4月1日‐平成20年3月31日）.zip, could not load 7 / 2846 
file:D:/Workshop_Data/securities/2008\1381_20080922_有価証券報告書‐第46期（平成19年7月1日‐平成20年6月30日）.zip, could not load 8 / 2846 
file:D:/Workshop_Data/securities/2008\1382_20080925_有価証券報告書‐第22期（

## 2. XBRLデータから財務情報を抽出

EDINETコードリストから、コードと業種を取得  
補助金の要素名：SubsidyIncomeNOI

In [24]:
def make_edinet_info_list(path):
    edinet_info = pd.read_csv(path, skiprows=1, encoding='cp932')
    edinet_info = edinet_info[['ＥＤＩＮＥＴコード', '提出者業種']]
    edinet_info_list = edinet_info.values.tolist()

    return edinet_info_list

code_list_path = '../../data/EDINET/code_list/EdinetcodeDlInfo.csv'
edinet_info_list = make_edinet_info_list(code_list_path)

XBRLデータの読み込み（処理が非常に重いので注意：１年でおよそ４時間）

In [37]:
def get_unit(fact):
    # (例) 'JPY / shares'
    if fact.unit is None:
        unit = None
    else:
        unit = fact.unit.value

    return unit

In [ ]:
def get_end_date(fact):
    if fact.context.endDatetime:
        # 終了日
        # (例) datetime.datetime(2020, 6, 1, 0, 0)
        # ※ (注意)
        # ・1日分だけ加算された日付になっていました。
        # ・また、開始日が無い時でも『instance 時点 (期末日) 』の
        #   日付が設定されました。
        #
        # XBRL ファイルに書かれているのと同じ日付の
        # 『終了日』を取得するときは、
        # 『fact.propertyView 属性』や
        # 『fact.context.propertyView 属性』の中から
        # 取得することができました。
        end_date = fact.context.endDatetime
    else:
        end_date = None

    return end_date

# factやタクソノミについてもう少し勉強した後で単位の調整を行う。

In [43]:
# XBRLファイルから補助金データを取得する
xbrl_path = 'D:/Workshop_Data/securities/**/*.xbrl'
xbrl_files = glob.glob(pathname=xbrl_path, recursive=True)
print(f'XBRLファイルの総数={len(xbrl_files)}, 1年あたり{round(len(xbrl_files) / (2021 - 2008 + 1))}ファイル')

for year in ['2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017_2021']:
    all_company_info_list = []
    xbrl_path = 'D:/Workshop_Data/securities/' + str(year) + '/**/*.xbrl'
    xbrl_files = glob.glob(pathname=xbrl_path, recursive=True)
    print(f'{year}年：XBRLファイルの総数={len(xbrl_files)}')

    for i, xbrl_file in enumerate(xbrl_files):
        edinet_code_filename = xbrl_file.split('-')[2] # ファイル名からEDINET_CODEを取得する
        edinet_code = ''
        firm_name = ''
        doc_title = ''
        fiscal_year = ''
        end_date = ''
        subsidy_noi = ''
        unit_subsidy_noi = ''
        subsidy_state = ''
        unit_subsidy_state = ''
        subsidy_ei = ''
        unit_subsidy_ei = ''
        subsidy_opeCF = ''
        unit_subsidy_opeCF = ''
        subsidy_proceeds_opeCF = ''
        unit_subsidy_proceeds_opeCF = ''
        subsidy_invCF = ''
        unit_subsidy_invCF = ''
        company_info_list = []

        ctrl = Cntlr.Cntlr()
        model_manager = ModelManager.initialize(ctrl)
        try:
            model_xbrl = model_manager.load(xbrl_file)
            print(f'EDINETコード：{edinet_code_filename}')
            if fact.context.endDatetime:
                print(f'終了日{fact.context.endDatetime}')
                end_date = fact.context.endDatetime

            for fact in model_xbrl.facts:
                if fact.concept.qname.localName == 'EDINETCodeDEI':
                    print(f'EDINETコード：{fact.value}')
                    edinet_code = fact.value
                
                elif fact.concept.qname.localName == 'FilerNameInJapaneseDEI':
                    print(f'企業名：{fact.value}')
                    firm_name = fact.value

                elif fact.concept.qname.localName == 'DocumentTitleCoverPage':
                    print(f'提出書類：{fact.value}')
                    doc_title = fact.value

                elif fact.concept.qname.localName == 'FiscalYearCoverPage':
                    print(f'事業年度{fact.value}')
                    fiscal_year = fact.value

                elif fact.concept.qname.localName == 'SubsidyIncomeNOI':
                    print(f'補助金収入_営業外収益：{fact.value}')
                    subsidy_noi = fact.value
                    unit_subsidy_noi = get_unit(fact)

                elif fact.concept.qname.localName == 'StateSubsidyEI':
                    print(f'国庫補助金_特別利益：{fact.value}')
                    subsidy_state = fact.value
                    unit_subsidy_state = get_unit(fact)

                elif fact.concept.qname.localName == 'SubsidyEI':
                    print(f'補助金収入_特別利益：{fact.value}')
                    subsidy_ei = fact.value
                    unit_subsidy_ei = get_unit(fact)

                elif fact.concept.qname.localName == 'SubsidyIncomeOpeCF':
                    print(f'営業CF_補助金収入：{fact.value}')
                    subsidy_opeCF = fact.value
                    unit_subsidy_opeCF = get_unit(fact)

                elif fact.concept.qname.localName == 'ProceedsFromSubsidyOpeCF':
                    print(f'営業CF_補助金受取額：{fact.value}')
                    subsidy_proceeds_opeCF = fact.value
                    unit_subsidy_proceeds_opeCF = get_unit(fact)

                elif fact.concept.qname.localName == 'SubsidiesReceivedInvCF':
                    print(f'投資CF_補助金受取額：{fact.value}')
                    subsidy_invCF = fact.value
                    unit_subsidy_inv_CF = get_unit(fact)

                elif fact.concept.qname.localName == 'GovernmentGrantIncomeIFRS':
                    print(f'IFRS_補助金収入: {fact.value}')
                    subsidy_IFRS = fact.value
                    unit_subsidy_IFRS = get_unit(fact)

            company_info_list.append(edinet_code_filename)
            company_info_list.append(edinet_code)
            company_info_list.append(firm_name)
            company_info_list.append(doc_title)
            company_info_list.append(fiscal_year)
            company_info_list.append(subsidy_noi)
            company_info_list.append(unit_subsidy_noi)
            company_info_list.append(subsidy_state)
            company_info_list.append(unit_subsidy_state)
            company_info_list.append(subsidy_ei)
            company_info_list.append(unit_subsidy_ei)
            company_info_list.append(subsidy_opeCF)
            company_info_list.append(unit_subsidy_opeCF)
            company_info_list.append(subsidy_proceeds_opeCF)
            company_info_list.append(unit_subsidy_proceeds_opeCF)
            company_info_list.append(subsidy_invCF)
            company_info_list.append(unit_subsidy_invCF)
            all_company_info_list.append(company_info_list)
            print(f'{i + 1} / {len(xbrl_files)} was successfully loaded.')
        except AttributeError:
            print(f'{i + 1} / {len(xbrl_files)} could not be loaded.')

    path = '../../intermediate/subsidy/' + str(year) + '.pickle'
    with open(path, mode='wb') as file:
        pickle.dump(obj=all_company_info_list, file=file)

XBRLファイルの総数=94844, 1年あたり6775ファイル
2008年：XBRLファイルの総数=7
EDINETコード：E03726
終了日2013-12-28 00:00:00
1 / 7 was successfully loaded.
EDINETコード：G04438
終了日2008-11-29 00:00:00
2 / 7 was successfully loaded.
EDINETコード：G04735
終了日2008-12-13 00:00:00
3 / 7 was successfully loaded.
EDINETコード：G04924
終了日2008-12-23 00:00:00
4 / 7 was successfully loaded.
EDINETコード：G03883
終了日2008-12-26 00:00:00
5 / 7 was successfully loaded.
EDINETコード：G02955
終了日2008-12-25 00:00:00
6 / 7 was successfully loaded.
EDINETコード：G03744
終了日2008-12-25 00:00:00
7 / 7 was successfully loaded.
2009年：XBRLファイルの総数=2013
EDINETコード：G04536
終了日2008-12-26 00:00:00
1 / 2013 was successfully loaded.
EDINETコード：G03817
終了日2009-01-27 00:00:00
2 / 2013 was successfully loaded.
EDINETコード：G04757
終了日2009-01-27 00:00:00
3 / 2013 was successfully loaded.
EDINETコード：G04467
終了日2009-01-30 00:00:00
4 / 2013 was successfully loaded.
EDINETコード：G04756
終了日2009-01-30 00:00:00
5 / 2013 was successfully loaded.
EDINETコード：G03405
終了日2009-01-29 00:00:00
6 / 2013 was succ

KeyboardInterrupt: 

In [47]:
df = pd.DataFrame(all_company_info_list, \
    columns=['EDINET_code', 'Firm_name', 'Industory', 'Subsidy'])
df.set_index('EDINET_code', inplace=True)
df = df.query("Subsidy != ''")
# df.dropna(subset=['Subsidy'], inplace=True)

In [48]:
df.to_csv('../../Data/EDINET/csv_data/subsidy_2020.csv', \
    encoding='cp932', header=True, index=True)

In [49]:
with open('all_company_info_list', 'wb') as file:
    pickle.dump(all_company_info_list, file)

with open('all_company_info_list', 'rb') as file:
    a = pickle.load(file)